In [ ]:
import pandas as pd
import numpy as np
from matplotlib import pyplot as plt
import gzip
import scipy.sparse as sparse
from susieinf import susie, cred
from scipy import linalg

In [ ]:
import rpy2
import rpy2.robjects.packages as rpackages
from rpy2.robjects.vectors import StrVector
from rpy2.robjects.packages import importr
utils = rpackages.importr('utils')
utils.chooseCRANmirror(ind=1)
from rpy2.robjects import conversion, default_converter
with conversion.localconverter(default_converter):
    packnames = ('susieR')
    # Load packages
    susieR = importr('susieR', suppress_messages=True)
import rpy2.robjects as ro
from rpy2.robjects import numpy2ri
numpy2ri.activate()
from rpy2.robjects import default_converter
np_cv_rules = default_converter + numpy2ri.converter
from rpy2.robjects.conversion import localconverter
from rpy2.rinterface_lib.callbacks import logger as rpy2_logger
import logging
rpy2_logger.setLevel(logging.ERROR) 

# Load in CAD GWAS and LD

In [ ]:
gwas_df = pd.read_csv('CAD_example.gwas.tsv.gz', delimiter='\t')
ld = np.load('CAD_example.ld.npz')['arr_0']
assert(len(gwas_df) == len(ld))

# Visualize GWAS

In [ ]:
fig,ax = plt.subplots(figsize=(10,3))
p1 = plt.scatter(gwas_df['position'], -np.log10(gwas_df['pvalue']), c = gwas_df['r2_to_lead'], cmap='Reds', alpha=0.5)
plt.colorbar(p1, label='LD to lead SNP')
plt.show()

# Fine-map this region using SuSiE and SuSiE-inf

In [ ]:
beta_rvec = rpy2.rinterface.FloatSexpVector(gwas_df['beta'].values)
se_rvec = rpy2.rinterface.FloatSexpVector(gwas_df['se'].values)
var_y = 1.0
nr,nc = ld.shape
LD_rvec = ro.r.matrix(ld, nrow=nr, ncol=nc)
N=360000

allowed_causal = 10
with localconverter(ro.default_converter + np_cv_rules) as cv:
    susie_results = susieR.susie_rss(bhat = beta_rvec, 
                                     shat = se_rvec, n = N, R = LD_rvec,
          var_y = var_y, L = allowed_causal, estimate_residual_variance = True)
susie_df = gwas_df[['variant','position','beta','se','pvalue']].copy()
susie_df['prob_susie'] = susie_results['pip']

fig,ax = plt.subplots(figsize=(10,2))
plt.scatter(susie_df['position'], susie_df['prob_susie'], alpha=0.5)
for cs in susie_results['sets']['cs']:
    cs_ind = [int(x)-1 for x in susie_results['sets']['cs'][cs]]
    cs_df = susie_df.loc[cs_ind,:]
    plt.scatter(cs_df['position'], cs_df['prob_susie'], alpha=0.7, label=cs)
plt.xlabel('SNP position')
plt.ylabel('SuSiE PIP')
plt.legend(title='Credible sets')
plt.show()

In [ ]:
eigenvals,V = linalg.eigh(ld)
Dsq = N * eigenvals
susieinf_results = susie(gwas_df['z'], var_y, 
                      N, allowed_causal, V=V, Dsq=Dsq, method='moments',
                      tausq_range=(1e-12,1.2),
                      est_tausq=True, est_sigmasq=True, verbose=False)
susieinf_df = gwas_df.copy()
susieinf_df['prob_susieinf'] = 1 - (1-susieinf_results['PIP']).prod(axis=1)
susieinf_results['cred'] = cred(susieinf_results['PIP'], coverage=0.95, purity=0.5, LD=None,V=V, Dsq=Dsq, n=N)

fig,ax = plt.subplots(figsize=(10,2))
plt.scatter(susieinf_df['position'], susieinf_df['prob_susieinf'], alpha=0.5)
for i,cs_ind in enumerate(susieinf_results['cred']):
    cs_df = susieinf_df.loc[cs_ind,:]
    plt.scatter(cs_df['position'], cs_df['prob_susieinf'], alpha=0.7, label=i)
plt.xlabel('SNP position')
plt.ylabel('SuSiE-inf PIP')
plt.legend(title='Credible sets')
plt.show()